# Deconvolution of the LArSoft opdet simulation.

### This notebook is used to analyse wvfs of the deconvolution module in larsoft. The output of the workflow is a collection of hits. The hits are then converted into a format that can be compared against the true photon information.

1. The wvfs are loaded. For a full comparison, the current "IDEAL" template is compared agains the "RAW" wvf generated from the arapuca temnplate and the "DEC" wvf generated from the deconvolution module (using both "GAUSS" and "WIENER" filters).

In [1]:
import sys; sys.path.insert(0, '../'); from lib.__init__ import *
# Load data according to type: RAW (digitized), DEC (deconvolved)
max_ev = 100
%time data0 = load_root_new("RAW","../data/Digispe100eve_ideal_10may_hist.root",    ["digispe","wavedigispe"],np.loadtxt("../template/MILANO/FBK/fbk_deco.txt"),max_ev=max_ev,label="IDEAL")
%time data1 = load_root_new("RAW","../data/Digispe100eve_template_10may_hist.root", ["digispe","wavedigispe"],np.loadtxt("../template/MILANO/FBK/fbk_deco.txt"),max_ev=max_ev,label="RAW")
%time data2 = load_root_new("DEC","../data/decon_gauss100eve_10may_hist.root",      ["digispe","opdecohana"], np.loadtxt("../template/MILANO/FBK/fbk_deco.txt"),max_ev=max_ev,label="GAUSS")
%time data3 = load_root_new("DEC","../data/decon_wiener100eve_aucale10may_hist.root",     ["digispe","opdecohana"], np.loadtxt("../template/MILANO/FBK/fbk_deco.txt"),max_ev=max_ev,label="WIENER")

# Select your favorite color map
color_map={data0["LABEL"]: "violet", data1["LABEL"]: "#3366CC", data2["LABEL"]: "#66AA00", data3["LABEL"]:"#FF9900"}
# sandybrown,seagreen,seashell,sienna,silver,skyblue,slateblue,slategray,slategrey,snow,springgreen,steelblue,tan,teal,thistle,tomato,turquoise,violet,wheat,white,whitesmoke,yellow,yellowgreen

2. The ophit data is loaded separetly. The ophit data is then converted into a format that can be compared against the true photons.

In [ ]:
# Load ophit data for each type
branches = ["Amplitude","EventID","OpChannel","PE","PeakTime"]
%time raw_reco0 = ophit_data("../data/ophitspe_ideal100eve_10may_hist.root",        scaling=1,label="IDEAL",   branches=branches,as_df=False)
%time raw_reco1 = ophit_data("../data/ophitspe_template100eve_10may_hist.root",     scaling=1,label="RAW",     branches=branches,as_df=False)
%time raw_reco2 = ophit_data("../data/ophitspe_gauss100eve_10may_hist.root",        scaling=100,label="GAUSS", branches=branches,as_df=False)
%time raw_reco3 = ophit_data("../data/ophitspe_wiener100eve_aucale10may_hist.root", scaling=100,label="WIENER",branches=branches,as_df=False)

%time reco0 = order_ophit_data(raw_reco0,max_ev,data0["RECO"]["CH"])
%time reco1 = order_ophit_data(raw_reco1,max_ev,data1["RECO"]["CH"])
%time reco2 = order_ophit_data(raw_reco2,max_ev,data2["RECO"]["CH"])
%time reco3 = order_ophit_data(raw_reco3,max_ev,data3["RECO"]["CH"])

['EventID', 'HitID', 'OpChannel', 'PeakTimeAbs', 'PeakTime', 'Frame', 'Width', 'Area', 'Amplitude', 'PE', 'FastToTotal']
CPU times: user 200 ms, sys: 8 ms, total: 208 ms
Wall time: 208 ms
['EventID', 'HitID', 'OpChannel', 'PeakTimeAbs', 'PeakTime', 'Frame', 'Width', 'Area', 'Amplitude', 'PE', 'FastToTotal']
CPU times: user 200 ms, sys: 4 ms, total: 204 ms
Wall time: 203 ms
['EventID', 'HitID', 'OpChannel', 'PeakTimeAbs', 'PeakTime', 'Frame', 'Width', 'Area', 'Amplitude', 'PE', 'FastToTotal']
CPU times: user 73.9 ms, sys: 0 ns, total: 73.9 ms
Wall time: 75.5 ms
['EventID', 'HitID', 'OpChannel', 'PeakTimeAbs', 'PeakTime', 'Frame', 'Width', 'Area', 'Amplitude', 'PE', 'FastToTotal']
CPU times: user 51.6 ms, sys: 3.89 ms, total: 55.5 ms
Wall time: 55.5 ms


3. Finally, the hits are compared against the true photons and exported to the same format as the wvf data.

In [ ]:
# Combine data and ophit data
%time ophit_0 = combine_data_ophit(data0,reco0)
%time ophit_1 = combine_data_ophit(data1,reco1)
%time ophit_2 = combine_data_ophit(data2,reco2)
%time ophit_3 = combine_data_ophit(data3,reco3)

CPU times: user 90 ms, sys: 3.84 ms, total: 93.9 ms
Wall time: 94.8 ms
CPU times: user 100 ms, sys: 7 µs, total: 100 ms
Wall time: 99.9 ms
CPU times: user 90.3 ms, sys: 4.09 ms, total: 94.4 ms
Wall time: 94.4 ms
CPU times: user 87.8 ms, sys: 3.99 ms, total: 91.8 ms
Wall time: 91.7 ms


### Visualize individual wvfs according to event, channel and wvf number.

In [ ]:
# Choose between a random channel number or select yourself
# ev = 1; ch = 218; wf = 1
ev = np.random.choice(data1["RECO"]["EV"])
ch = np.random.choice(data1["RECO"]["CH"][data1["RECO"]["EV"] == ev])
wf = np.random.choice(data1["RECO"]["#WVF"][(data1["RECO"]["EV"] == ev)*(data1["RECO"]["CH"] == ch)])

# Find the index of the channel number in the data
try:
    num0 = np.where((data0["RECO"]["EV"] == ev)*(data0["RECO"]["CH"] == ch)*(data0["RECO"]["#WVF"] == wf))[0][0]
except:
    num0 = 0
    print("No ideal data for %s %s %s"%(ev,ch,wf))
    
num1 = np.where((data1["RECO"]["EV"] == ev)*(data1["RECO"]["CH"] == ch)*(data1["RECO"]["#WVF"] == wf))[0][0]

# Genarte figure with subplots
fig = make_subplots(rows=2, cols=2,subplot_titles=('', ''))

# Add waveform traces to the figure
fig.add_trace(go.Scatter(line=dict(color=color_map[data0["LABEL"]]),name="%s #PE: %.2f"%(data1["LABEL"],data0["RECO"]["PE"][num0]),x=1e6*16e-9*(np.linspace(0,1000,1001))+data0["RECO"]["WVF_IX"][num0],y=data0["RECO"]["WVF"][num0]-data0["PEDESTAL"]),col=1,row=1)
fig.add_trace(go.Scatter(line=dict(color=color_map[data1["LABEL"]]),name="%s #PE: %.2f"%(data1["LABEL"],data1["RECO"]["PE"][num1]),x=1e6*16e-9*(np.linspace(0,1000,1001))+data1["RECO"]["WVF_IX"][num1],y=data1["RECO"]["WVF"][num1]-data1["PEDESTAL"]),col=2,row=1)
fig.add_trace(go.Scatter(line=dict(color=color_map[data2["LABEL"]]),name="%s #PE: %.2f"%(data2["LABEL"],data2["RECO"]["PE"][num1]),x=1e6*16e-9*(np.linspace(0,1000,1001))+data2["RECO"]["WVF_IX"][num1],y=data2["RECO"]["WVF"][num1]),col=1,row=2)
fig.add_trace(go.Scatter(line=dict(color=color_map[data3["LABEL"]]),name="%s #PE: %.2f"%(data3["LABEL"],data3["RECO"]["PE"][num1]),x=1e6*16e-9*(np.linspace(0,1000,1001))+data3["RECO"]["WVF_IX"][num1],y=data3["RECO"]["WVF"][num1]),col=2,row=2)

# Add vertical lines according to the reconstructed T0
fig.add_vline(x=data0["RECO"]["T0"][num0], line_width=2, line_dash="dash", line_color="gray",col=1,row=1)
fig.add_vline(x=data1["RECO"]["T0"][num1], line_width=2, line_dash="dash", line_color="gray",col=2,row=1)
fig.add_vline(x=data2["RECO"]["T0"][num1], line_width=2, line_dash="dash", line_color="gray",col=1,row=2)
fig.add_vline(x=data3["RECO"]["T0"][num1], line_width=2, line_dash="dash", line_color="gray",col=2,row=2)

# Add true PE times to the figure
# if len(data0["TRUE"]["PETIMES"][num0]) > 100:
# fig.add_trace(go.Histogram(name="TRUE #PE: %.2f"%(len(data0["TRUE"]["PETIMES"][num0])),x=np.asarray(data0["TRUE"]["PETIMES"][num0])),col=1,row=1)
# fig.add_trace(go.Histogram(name="TRUE #PE: %.2f"%(len(data1["TRUE"]["PETIMES"][num1])),x=np.asarray(data1["TRUE"]["PETIMES"][num1])),col=2,row=1)
# else:
fig.add_trace(go.Scatter(marker_symbol="triangle-up",mode="markers",line=dict(color="black"),name="TRUE #PE: %.2f"%(len(data0["TRUE"]["PETIMES"][num0])),x=np.asarray(data0["TRUE"]["PETIMES"][num0]),y=np.zeros(len(data0["TRUE"]["PETIMES"][num0]))),col=1,row=1)
fig.add_trace(go.Scatter(marker_symbol="triangle-up",mode="markers",line=dict(color="black"),name="TRUE #PE: %.2f"%(len(data1["TRUE"]["PETIMES"][num1])),x=np.asarray(data1["TRUE"]["PETIMES"][num1]),y=np.zeros(len(data1["TRUE"]["PETIMES"][num1]))),col=2,row=1)
fig.add_trace(go.Scatter(marker_symbol="triangle-up",mode="markers",line=dict(color="black"),name="TRUE #PE: %.2f"%(len(data1["TRUE"]["PETIMES"][num1])),x=np.asarray(data1["TRUE"]["PETIMES"][num1]),y=np.zeros(len(data1["TRUE"]["PETIMES"][num1]))),col=1,row=2)
fig.add_trace(go.Scatter(marker_symbol="triangle-up",mode="markers",line=dict(color="black"),name="TRUE #PE: %.2f"%(len(data1["TRUE"]["PETIMES"][num1])),x=np.asarray(data1["TRUE"]["PETIMES"][num1]),y=np.zeros(len(data1["TRUE"]["PETIMES"][num1]))),col=2,row=2)

# Add ophits to the figure
fig.add_trace(go.Scatter(name="OPHITFINDER #PE: %.2f"%(ophit_0["PE"][num0]),line=dict(color="#DC3912"),mode="markers",x=ophit_0["TIMES"][num0],y=ophit_0["AMP"][num0]/reco0["SCALING"]),col=1,row=1)
fig.add_trace(go.Scatter(name="OPHITFINDER #PE: %.2f"%(ophit_1["PE"][num1]),line=dict(color="#DC3912"),mode="markers",x=ophit_1["TIMES"][num1],y=ophit_1["AMP"][num1]/reco1["SCALING"]),col=2,row=1)
fig.add_trace(go.Scatter(name="OPHITFINDER #PE: %.2f"%(ophit_2["PE"][num1]),line=dict(color="#DC3912"),mode="markers",x=ophit_2["TIMES"][num1],y=ophit_2["AMP"][num1]/reco2["SCALING"]),col=1,row=2)
fig.add_trace(go.Scatter(name="OPHITFINDER #PE: %.2f"%(ophit_3["PE"][num1]),line=dict(color="#DC3912"),mode="markers",x=ophit_3["TIMES"][num1],y=ophit_3["AMP"][num1]/reco3["SCALING"]),col=2,row=2)

# Update the layout
fig.update_layout(title="Comparison for ev %i, ch %i and wvf %i"%(ev,ch,wf),xaxis_title="Time in [&mu;s]",yaxis_title="Amp. in [ADC]",xaxis2_title="Time in [&mu;s]",yaxis2_title="Amp. in [a.u.]",xaxis3_title="Time in [&mu;s]",yaxis3_title="Amp. in [a.u.]",xaxis4_title="Time in [&mu;s]",yaxis4_title="Amp. in [a.u.]")
fig.update_layout(autosize=True,height=600,font=dict(size=14))
fig.update_layout(template="presentation")
# fig.update_yaxes(type="log")
fig.show()

No ideal data for 4 303 1


### Calculate further variables and formar data to generate a dataframe.

In [ ]:
with np.errstate(divide='ignore', invalid='ignore'):
    pe_error_0 = (np.asarray(data0["RECO"]["PE"])-np.asarray(data0["TRUE"]["PE"]))/np.asarray(data0["TRUE"]["PE"])
    pe_error_1 = (np.asarray(data1["RECO"]["PE"])-np.asarray(data1["TRUE"]["PE"]))/np.asarray(data1["TRUE"]["PE"])
    pe_error_2 = (np.asarray(data2["RECO"]["PE"])-np.asarray(data1["TRUE"]["PE"]))/np.asarray(data1["TRUE"]["PE"])
    pe_error_3 = (np.asarray(data3["RECO"]["PE"])-np.asarray(data1["TRUE"]["PE"]))/np.asarray(data1["TRUE"]["PE"])
    ophitpe_error_0 = (np.asarray(ophit_0["PE"])-np.asarray(data0["TRUE"]["PE"]))/np.asarray(data0["TRUE"]["PE"])
    ophitpe_error_1 = (np.asarray(ophit_1["PE"])*7.5-np.asarray(data1["TRUE"]["PE"]))/np.asarray(data1["TRUE"]["PE"])
    ophitpe_error_2 = (np.asarray(ophit_2["PE"])-np.asarray(data1["TRUE"]["PE"]))/np.asarray(data1["TRUE"]["PE"])
    ophitpe_error_3 = (np.asarray(ophit_3["PE"])-np.asarray(data1["TRUE"]["PE"]))/np.asarray(data1["TRUE"]["PE"])

    t0_reco_0 = np.asarray(data0["RECO"]["T0"])-np.asarray(data0["TRUE"]["T0"])
    t0_reco_1 = np.asarray(data1["RECO"]["T0"])-np.asarray(data1["TRUE"]["T0"])
    t0_reco_2 = np.asarray(data2["RECO"]["T0"])-np.asarray(data1["TRUE"]["T0"])
    t0_reco_3 = np.asarray(data3["RECO"]["T0"])-np.asarray(data1["TRUE"]["T0"])

    ev            = np.concatenate([data0["RECO"]["EV"],  data1["RECO"]["EV"],  data2["RECO"]["EV"],  data3["RECO"]["EV"]])
    ch            = np.concatenate([data0["RECO"]["CH"],  data1["RECO"]["CH"],  data2["RECO"]["CH"],  data3["RECO"]["CH"]])
    wvf           = np.concatenate([data0["RECO"]["#WVF"],data1["RECO"]["#WVF"],data2["RECO"]["#WVF"],data3["RECO"]["#WVF"]])
    pe_reco       = np.concatenate([data0["RECO"]["PE"],  data1["RECO"]["PE"],  data2["RECO"]["PE"],  data3["RECO"]["PE"]])
    pe_true       = np.concatenate([data0["TRUE"]["PE"],  data1["TRUE"]["PE"],  data1["TRUE"]["PE"],  data1["TRUE"]["PE"]])
    pe_ophit      = np.concatenate([ophit_0["PE"],        ophit_1["PE"],        ophit_2["PE"],        ophit_3["PE"]])
    ophitpe_error = np.concatenate([ophitpe_error_0,      ophitpe_error_1,      ophitpe_error_2,      ophitpe_error_3])
    pe_error      = np.concatenate([pe_error_0,           pe_error_1,           pe_error_2,           pe_error_3])
    t0_reco       = np.concatenate([t0_reco_0,            t0_reco_1,            t0_reco_2,            t0_reco_3])
    filter_label  = np.concatenate([[data0["LABEL"]]*len(pe_error_0),[data1["LABEL"]]*len(pe_error_1),[data2["LABEL"]]*len(pe_error_2),[data3["LABEL"]]*len(pe_error_3)])

    df = pd.DataFrame({ "EV":ev,
                        "CH":ch,
                        "WVF":wvf,
                        "FILTER":filter_label,
                        "ERROR PE":pe_error,
                        "ERROR OPHIT PE":ophitpe_error,
                        "TRUE PE":pe_true,
                        "RECO PE":pe_reco, 
                        "OPHIT PE":pe_ophit,
                        "AMP [a.u.]":amp,
                        "RECO T0":t0_reco})

### This plot includes a linear fit to the data. It can be used to calibrate different features of the ophitfinder algorith (e.g. SPE_SHIFT)

In [ ]:
fig = px.scatter(data_frame=df[(df['TRUE PE'] > 10)*(df['TRUE PE'] < 1000)], 
                x="AMP [a.u.]",
                y='TRUE PE',
                color='FILTER',
                color_discrete_map=color_map,
                # marginal_x='box',
                hover_data=["EV","CH","WVF"],
                trendline="ols")
fig.update_layout(autosize=True,height=800,font=dict(size=16),template="presentation")
fig.show()

results = px.get_trendline_results(fig) # print(results)
results.query("FILTER == 'GAUSS'").px_fit_results.iloc[0].summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.991
Model:                            OLS   Adj. R-squared:                  0.991
Method:                 Least Squares   F-statistic:                 2.611e+05
Date:                Mon, 15 May 2023   Prob (F-statistic):               0.00
Time:                        14:08:44   Log-Likelihood:                -10187.
No. Observations:                2251   AIC:                         2.038e+04
Df Residuals:                    2249   BIC:                         2.039e+04
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         14.4952      0.618     23.438      0.000      13.282      15.708
x1            25.5205      0.050    511.019      0.000      25.423      25.618
==============================================================================
Omnibus:                      237.784   Durbin-Watson:                   1.604
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             1969.825
Skew:                           0.029   Prob(JB):                         0.00
Kurtosis:                       7.582   Cond. No.                         16.3
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

### This is a scatter plot. It can be used to display differnet variables in terms of the true photon information.

In [ ]:
fig = px.scatter(data_frame=df[(df['TRUE PE'] > 10)*(df['TRUE PE'] < 2000)], 
                x="ERROR OPHIT PE",
                y="TRUE PE",
                color='FILTER',
                color_discrete_map=color_map,
                marginal_x='box',
                hover_data=["EV","CH","WVF"],
                # marginal_y='histogram',
                template="presentation")
fig.update_layout(autosize=True,height=800,font=dict(size=16))
fig.update_traces(opacity=0.75)
fig.show()

### Gauss fit to histogram. This can be used to calculate the SPE resolution.

In [ ]:
this_df = df[(df["TRUE PE"] > 100)*(df["TRUE PE"] < 200)]
variable = "ERROR OPHIT PE"
xlim=(1,99)
data = []
acc = 20
fig,data = gauss_fit_distribution(this_df,this_bin=750,variable=variable,color="FILTER",color_map=color_map,output_data=data,xlim=xlim,acc=20)
fig.update_layout(bargap = 0,
                # yaxis = dict(range= [0,50])
                )
fig.show()

### The same gaussian plot can be applyed to a range of bins and the data exported to a dataframe for further analysis.

In [ ]:
pe_bins = np.concatenate([np.arange(10,100,10),np.arange(100,1000,100),np.arange(1000,2000,500)])
fig,data = get_gauss_fit_data(df,"TRUE PE",pe_bins,"ERROR OPHIT PE","FILTER",color_map,xlim=(1,90),acc=20,terminal=False)
fit_df = pd.DataFrame(data)
display(fit_df)
fit_df["SQRT_PE"] = np.sqrt(fit_df["THIS_PE"])

FILTER  THIS_PE       AMP   AMP_ERR      MEAN  MEAN_ERR       STD  \
0    IDEAL     15.0  0.090783  0.008546 -0.066828  0.018035  0.164265   
1      RAW     15.0  0.113511  0.010237  0.082192  0.064784  0.530712   
2    GAUSS     15.0  0.130425  0.014066 -0.020264  0.023192  0.186099   
3   WIENER     15.0  0.082901  0.006780 -0.169695  0.024629  0.232514   
4    IDEAL     25.0  0.091097  0.008373 -0.055678  0.011840  0.111551   
..     ...      ...       ...       ...       ...       ...       ...   
71  WIENER    950.0  0.084596  0.013180 -0.004763  0.002027  0.010888   
72   IDEAL   1250.0  0.076097  0.014015 -0.004652  0.001474 -0.005173   
73     RAW   1250.0  0.075611  0.011701 -0.009052  0.007973 -0.041085   
74   GAUSS   1250.0  0.127538  0.011517 -0.008341  0.000888  0.008515   
75  WIENER   1250.0  0.121095  0.015064 -0.008285  0.001303 -0.009078   

     STD_ERR  
0   0.019543  
1   0.072464  
2   0.024018  
3   0.028673  
4   0.012608  
..       ...  
71  0.002273  
72  0.001721  
73  0.009828  
74  0.000889  
75  0.001313  

[76 rows x 8 columns]

In [ ]:
display(fit_df)
fig = px.scatter(fit_df,x="SQRT_PE",
                y="STD",
                color="FILTER",
                color_discrete_sequence=pd.Series(fit_df["FILTER"].unique()).map(color_map),
                # trendline="ols",
                )
fig.update_layout(template="presentation")
# results = px.get_trendline_results(fig) # print(results)
# results.query("FILTER == 'GAUSS'").px_fit_results.iloc[0].summary()
fig.show()

FILTER  THIS_PE       AMP   AMP_ERR      MEAN  MEAN_ERR       STD  \
0    IDEAL     15.0  0.090783  0.008546 -0.066828  0.018035  0.164265   
1      RAW     15.0  0.113511  0.010237  0.082192  0.064784  0.530712   
2    GAUSS     15.0  0.130425  0.014066 -0.020264  0.023192  0.186099   
3   WIENER     15.0  0.082901  0.006780 -0.169695  0.024629  0.232514   
4    IDEAL     25.0  0.091097  0.008373 -0.055678  0.011840  0.111551   
..     ...      ...       ...       ...       ...       ...       ...   
71  WIENER    950.0  0.084596  0.013180 -0.004763  0.002027  0.010888   
72   IDEAL   1250.0  0.076097  0.014015 -0.004652  0.001474 -0.005173   
73     RAW   1250.0  0.075611  0.011701 -0.009052  0.007973 -0.041085   
74   GAUSS   1250.0  0.127538  0.011517 -0.008341  0.000888  0.008515   
75  WIENER   1250.0  0.121095  0.015064 -0.008285  0.001303 -0.009078   

     STD_ERR    SQRT_PE  
0   0.019543   3.872983  
1   0.072464   3.872983  
2   0.024018   3.872983  
3   0.028673   3.872983  
4   0.012608   5.000000  
..       ...        ...  
71  0.002273  30.822070  
72  0.001721  35.355339  
73  0.009828  35.355339  
74  0.000889  35.355339  
75  0.001313  35.355339  

[76 rows x 9 columns]

### This shows a regular histogram.

In [ ]:
fig = px.histogram(data_frame=df[(df['TRUE PE'] > 0)*(df['TRUE PE'] < 1000)],
                    x="RECO T0",
                    color='FILTER',
                    color_discrete_map=color_map,
                    barmode="overlay",
                    marginal='box',
                    template="presentation",
                    nbins=2000,
                    range_x=[-0.16,0.32])
fig.update_layout(autosize=True,height=800,font=dict(size=16))
fig.update_layout(bargap=0)
fig.show()

### Finally a scintillation fit of the deconvolved wvfs is shown.

In [ ]:
min_wvf_length = 500
ave_wvfs = []
for data in [data2,data3]:

    # Select only the waveforms with a minimum length
    data["RECO"]["SHORT_WVF"] = []
    for wvf in data["RECO"]["WVF"]:
        if len(wvf) > min_wvf_length:
            data["RECO"]["SHORT_WVF"].append(wvf[:min_wvf_length])

    # Prepare the averaged deconvolved waveforms for the scintillation profile fit
    ave_wvf = np.mean(np.asarray(data["RECO"]["SHORT_WVF"]),axis=0)
    ave_wvf = ave_wvf/np.max(ave_wvf)
    ave_wvf = ave_wvf[np.argmax(ave_wvf):]
    ave_wvfs.append(ave_wvf)
    
    # Fit the scintillation profile of the averaged deconvolved waveforms
    initial = [0.7,0.3,6,1400]
    labels = ["CONSTANT","AMPLITUDE","TAU FAST","TAU SLOW"]
    popt, pcov = curve_fit(scint_profile,16*np.arange(len(ave_wvf)),ave_wvf,p0=initial)
    perr = np.sqrt(np.diag(pcov))

    # Print the fit results
    ave_wvfs.append(scint_profile(16*np.arange(len(ave_wvf)),*popt))
    print("\n----------- FIT VALUES " + data["LABEL"]+ " ------------")
    for i in range(len(initial)):
        print("%s:\t%.2E\t%.2E"%(labels[i], popt[i], perr[i]))
    print("-----------------------------------------")


----------- FIT VALUES GAUSS ------------
CONSTANT:	1.84E+02	1.93E+00
AMPLITUDE:	1.81E-01	3.14E-03
TAU FAST:	7.11E+01	1.25E+00
TAU SLOW:	1.68E+03	3.54E+01
-----------------------------------------

----------- FIT VALUES WIENER ------------
CONSTANT:	1.84E+02	1.93E+00
AMPLITUDE:	1.81E-01	3.05E-03
TAU FAST:	7.08E+01	1.20E+00
TAU SLOW:	1.74E+03	3.65E+01
-----------------------------------------


In [ ]:
# Generate the dataframe for the plot
wvfs  = np.concatenate([ave_wvfs[0],ave_wvfs[1],ave_wvfs[2],ave_wvfs[3]])
wvfs_x  = np.concatenate([16*np.arange(len(ave_wvf)),16*np.arange(len(ave_wvf)),16*np.arange(len(ave_wvf)),16*np.arange(len(ave_wvf))])
fit_label  = np.concatenate([["WVF"]*len(ave_wvf),["FIT"]*len(ave_wvf),["WVF"]*len(ave_wvf),["FIT"]*len(ave_wvf)])
filter_label  = np.concatenate([[data2["LABEL"]]*len(ave_wvf),[data2["LABEL"]]*len(ave_wvf),[data3["LABEL"]]*len(ave_wvf),[data3["LABEL"]]*len(ave_wvf)])

fit_df = pd.DataFrame({"WVF":wvfs,"TIME in [ns]":wvfs_x,"FILTER":filter_label,"FIT":fit_label})

# Plot the results
fig = px.line(data_frame=fit_df,x="TIME in [ns]",y="WVF",color="FIT",facet_col="FILTER",log_y=True,color_discrete_map=color_map)
fig.show()